In [10]:
# CFM 301 W23
# Final Project
# Keshav, Andrew, Gavin, Anson

import pandas as pd
import numpy as np

In [11]:

# noOfMAActivity (custom factor)
# STOCK_SPLIT (custom factor)
# DIVAMT (custom factor - raw data point)
# SPREAD (custom factor - raw data point)

# Profitability
# O_SCORE_Q	- A.4.25 Oq 1, Oq 6, and Oq 12, Quarterly O-score (Ohlson, 1980 as cited in Hou, Xue, Zhang, 2018)

# Intangibles
# HIRING_RATE - A.5.10 Hn, hiring rate. (Belo, Lin, and Bazdresch, 2014 as cited in Hou, Xue, Zhang, 2018)

# Investment
# INVESTMENT_GROWTH_3Y - A.3.9 3Ig, 3-year investment growth (Hou, Xue, Zhang, 2018)

In [12]:
an_compustat = pd.read_excel("dataset_files/compustat_quarter.xlsx", sheet_name="compustat")
an_compustat.columns = ["GVKEY", "DATE", "DATEYEAR", "DATEQUARTER", "INDF", "LevelOfConsol", "PopScore", "DataFormat", "CUSIP", "CONM", "ISOCurrencyCode", "YYYYQQ_1", "YYYYQQ_2", "ACTQ", "ATQ", "DLCQ", "DLTTQ", "DPQ", "LCTQ", "LTQ", "NIQ", "PIQ", "SALEQ", "CAPXY", "ACTIVE/INACTIVE"]
an_compustat["DATE"] = pd.to_datetime(an_compustat["DATE"])


an_compustat.sort_values(["DATEYEAR"])
an_compustat['NIQ_4'] = an_compustat.groupby(["CUSIP"])["NIQ"].shift(4)

print(an_compustat)


# total assets
an_compustat["TA_Q"] = an_compustat["ATQ"]

# leverage ratio
an_compustat["TLTA_Q"] = (an_compustat["DLCQ"] + an_compustat["DLTTQ"])/an_compustat["TA_Q"]

an_compustat["WCTA_Q"] = (an_compustat["ACTQ"] - an_compustat["LCTQ"])/an_compustat["TA_Q"]

an_compustat["CLCA_Q"] = an_compustat["LCTQ"]/an_compustat["ACTQ"]

an_compustat["OENEG_Q"] = an_compustat["LTQ"] > an_compustat["TA_Q"]

an_compustat["NITA_Q"] = an_compustat["NIQ"]/an_compustat["TA_Q"]

an_compustat["FUTL_Q"] = (an_compustat["PIQ"] + an_compustat["DPQ"])/an_compustat["LTQ"]

an_compustat["IN2_Q"] = (an_compustat["NIQ"] < 0) & (an_compustat["NIQ_4"] < 0)

an_compustat["CHIN_Q"] = (an_compustat["NIQ"] - an_compustat["NIQ_4"])/(abs(an_compustat["NIQ"]) + abs(an_compustat["NIQ_4"]))

groupByYear = an_compustat.groupby(["DATEYEAR"])

print(max(an_compustat["TA_Q"]))

groupByYear = an_compustat.groupby(["DATEYEAR"])
# winsorized on a yearly basis
for curYear, groupedYear in groupByYear:
    for variable in ["TA_Q", "TLTA_Q", "WCTA_Q", "CLCA_Q", "NITA_Q", "FUTL_Q", "CHIN_Q"]:
        lower = groupedYear[variable].quantile(0.01)
        upper = groupedYear[variable].quantile(0.99)
        an_compustat.loc[an_compustat["DATEYEAR"] == curYear, variable] = an_compustat.loc[an_compustat["DATEYEAR"] == curYear, variable].clip(lower, upper)

print(max(an_compustat["TA_Q"]))

an_compustat["O_SCORE_Q"] = -1.32 -0.407*np.log(an_compustat["TA_Q"])+ 6.03*an_compustat["TLTA_Q"]-1.43*an_compustat["WCTA_Q"] +0.076*an_compustat["CLCA_Q"]-1.720*an_compustat["OENEG_Q"]-2.37*an_compustat["NITA_Q"]-1.83*an_compustat["FUTL_Q"] +0.285*an_compustat["IN2_Q"]-0.521*an_compustat["CHIN_Q"]

# Shift the Ohlson's O-Score by one quarter to account for the lag on reporting delay
an_compustat['O_SCORE_Q'] = an_compustat.groupby(["CUSIP"])["O_SCORE_Q"].shift(1)
an_compustat.sort_values(["YYYYQQ_1"])


print(an_compustat[["CUSIP", "DATEYEAR", "DATEQUARTER", "YYYYQQ_1", "NIQ", "NIQ_4", "O_SCORE_Q"]])

         GVKEY       DATE  DATEYEAR  DATEQUARTER  INDF LevelOfConsol PopScore  \
0         1045 1979-03-31      1979          1.0  INDL             C        D   
1         1045 1979-06-30      1979          2.0  INDL             C        D   
2         1045 1979-09-30      1979          3.0  INDL             C        D   
3         1045 1979-12-31      1979          4.0  INDL             C        D   
4         1045 1980-03-31      1980          1.0  INDL             C        D   
...        ...        ...       ...          ...   ...           ...      ...   
148973  326688 2019-12-31      2019          4.0  INDL             C        D   
148974  326688 2020-03-31      2020          1.0  INDL             C        D   
148975  326688 2020-06-30      2020          2.0  INDL             C        D   
148976  326688 2020-09-30      2020          3.0  INDL             C        D   
148977  326688 2020-12-31      2020          4.0  INDL             C        D   

       DataFormat      CUSI

In [13]:
an_compustat_yearly = pd.read_excel("dataset_files/compustat_annual.xlsx", sheet_name="fundamentals")
an_compustat_yearly.columns = ["GVKEY", "DATE", "DATEYEAR", "INDF", "LevelOfConsol", "PopScore", "DataFormat", "CUSIP", "CONAM", "ISOCurrencyCode", "ACT", "AT", "CAPX", "DLC", "DLTT", "DP", "EMP", "LCT", "LT", "NI", "PI", "SALE", "ACTIVE/INACTIVE"]
an_compustat_yearly["DATE"] = pd.to_datetime(an_compustat["DATE"])

an_compustat_yearly.sort_values(["DATEYEAR"])

# Data is included if we also choose to calculate Ohlson's O-Score on an annual basis although since quarterly data is provided not necessary

# EMP (Employee) data is only provided hence why I have to calculate this factor on an annual basis
an_compustat_yearly['EMP_1'] = an_compustat_yearly.groupby(["CUSIP"])["EMP"].shift(1)

an_compustat_yearly["HIRING_RATE"] = ((an_compustat_yearly['EMP'] / an_compustat_yearly['EMP_1'])-1)

an_compustat_yearly.sort_values(["DATEYEAR"])

# Shift the Hiring Rate by one year to account for the lag on reporting delay
an_compustat_yearly["HIRING_RATE"] = an_compustat_yearly.groupby(["CUSIP"])["HIRING_RATE"].shift(1)


In [14]:
# INVESTMENT_GROWTH_3Y
# Capital Expenditures from Last Year (t-1)
an_compustat_yearly['CAPX_1'] = an_compustat_yearly.groupby(["CUSIP"])["CAPX"].shift(1)
# Capital Expenditures from Four Years Ago (t-5)
an_compustat_yearly['CAPX_4'] = an_compustat_yearly.groupby(["CUSIP"])["CAPX"].shift(4)

# Three Year Investment Growth
an_compustat_yearly["INVESTMENT_GROWTH_3Y"] = ((an_compustat_yearly['CAPX_1'] / an_compustat_yearly['CAPX_4'])-1)


In [15]:
crsp_monthly = pd.read_excel("dataset_files/crsp_monthly.xlsx", sheet_name="monthly")
crsp_monthly.columns = ["PERMNO", "DATE", "CONM", "cusip", "DIVAMT", "CFACSHR", "SPREAD"]
crsp_monthly["DATE"] = pd.to_datetime(crsp_monthly["DATE"])
crsp_monthly["monthid"] = (crsp_monthly.DATE.dt.year - 1980) * 12 + crsp_monthly.DATE.dt.month
crsp_monthly["yyyymm"] = crsp_monthly.DATE.dt.year * 100 + crsp_monthly.DATE.dt.month

crsp_monthly['CFACSHR_1'] = crsp_monthly.groupby(["cusip"])["CFACSHR"].shift(1)

crsp_monthly["STOCK_SPLIT"] = crsp_monthly['CFACSHR'] / crsp_monthly['CFACSHR_1']

print(crsp_monthly[["cusip", "monthid", "STOCK_SPLIT", "DIVAMT", "SPREAD"]])

           cusip  monthid  STOCK_SPLIT  DIVAMT  SPREAD
0       46603210       73          NaN     NaN     NaN
1       46603210       74          NaN     NaN     0.5
2       46603210       75          1.0     NaN     1.5
3       46603210       76          1.0     NaN     1.5
4       46603210       77          1.0     NaN     NaN
...          ...      ...          ...     ...     ...
414657  12503M10      488          1.0    0.42     NaN
414658  12503M10      489          1.0     NaN     NaN
414659  12503M10      490          1.0     NaN     NaN
414660  12503M10      491          1.0    0.42     NaN
414661  12503M10      492          1.0     NaN     NaN

[414662 rows x 5 columns]


In [16]:
# M&A Activity (Including Repurchases and Buybacks)

ma_data = pd.read_excel("dataset_files/M&A_events.xlsx", sheet_name="tr_sdc_ma")
ma_data.columns = ["DEALNO", "EVENT_DATE", "EVENT_DESC", "TARGET_NAME_1", "ACQUIROR_NAME_1", "ANNOUNCE_DATE", "TARGET_NAME", "ACQUIROR_NAME", "ACQUIROR_CUSIP", "TARGET_CUSIP"]
ma_data["ANNOUNCE_DATE"] = pd.to_datetime(ma_data["ANNOUNCE_DATE"])
ma_data["monthid"] = (ma_data.ANNOUNCE_DATE.dt.year - 1980) * 12 + ma_data.ANNOUNCE_DATE.dt.month
ma_data["yyyymm"] = ma_data.ANNOUNCE_DATE.dt.year * 100 + ma_data.ANNOUNCE_DATE.dt.month
print(ma_data[["monthid", "ANNOUNCE_DATE"]])

maActivityData = {'monthid':[], 'cusip': [], 'noOfMAActivity':[]}


monthCUSIPGroups = ma_data.groupby(['monthid', 'ACQUIROR_CUSIP'])

for [monthID, cusip], monthGroup in monthCUSIPGroups:
    print(monthGroup)
    maActivityData['monthid'].append(monthID)
    maActivityData['cusip'].append(cusip)
    maActivityData['noOfMAActivity'].append(monthGroup.shape[0])

maActivityData = pd.DataFrame(maActivityData)
maActivityData.sort_values(["monthid", "cusip"])

      monthid ANNOUNCE_DATE
0         244    2000-04-26
1         233    1999-05-12
2         244    2000-04-27
3         245    2000-05-04
4         245    2000-05-04
...       ...           ...
9008      461    2018-05-02
9009      461    2018-05-22
9010      461    2018-05-16
9011      453    2017-09-19
9012      462    2018-06-06

[9013 rows x 2 columns]
        DEALNO EVENT_DATE                                         EVENT_DESC  \
825  124852020 1983-11-16                  Offers $29 per share or $86.5 mil   
826  124852020 1983-11-30                                  Offer is rejected   
827  124852020 1983-12-01                        Increased offer is rejected   
828  124852020 1983-12-08  New Jersey Resources tries to stop NYT from so...   
829  124852020 1984-02-01                 Court allows soliciting of proxies   
830  124852020 1984-02-02                 Holders meet to decide proxy fight   
831  124852020 1984-02-09       Losses proxy fight Receives only 38% of vote   

monthid   cusip  noOfMAActivity
0          47  629430               8
1          47  838518               1
2          49  191216               1
3          63  501044               1
4          65  115637               1
...       ...     ...             ...
4793      461  886547               1
4794      461  91529Y               1
4795      461  V7780T               1
4796      462  91324P               1
4797      508  5M5306               2

[4798 rows x 3 columns]

In [19]:
def convertToQuarter(x):
    if ((x % 3) == 0): return x/3
    else: return ((x//3)+1)

originalDataset = pd.read_sas("dataset_files/provided_dataset_merged_df.sas7bdat", encoding="ISO-8859-1")
originalDataset['permno'] = originalDataset['permno'].astype(np.int64)

print(originalDataset.shape)
print(originalDataset['beta_5y'].mean())


# Since the Thomson/Refinitive Data only provides a CUSIP for the company in question (6 digit CUSIP I have utilized the CUSIP on a company basis)
originalDataset['cusip6'] = originalDataset.cusip.astype(str).str[:6]
# Since the Monthly CRSP Data only provides a CUSIP for the company in question plus security without the 9th check digit (8 digit CUSIP I have chopped of the check digit)
originalDataset['cusip8'] = originalDataset.cusip.astype(str).str[:8]
originalDataset['YEAR'] = originalDataset.yyyymm.astype(str).str[:4].astype(np.int64)
originalDataset['MONTH'] = originalDataset.yyyymm.astype(str).str[4:6].astype(np.int64)
originalDataset['QUARTER'] = originalDataset['MONTH'].transform(lambda x: convertToQuarter(x)).astype(np.int64)

originalDataset['yyyyqq'] = originalDataset['YEAR'].astype(str) + "Q" + originalDataset['QUARTER'].astype(str)

print(originalDataset.shape)
print(originalDataset['beta_5y'].mean())

# Merging maActivityData
maActivityData.columns = ["monthid", "cusip6", "noOfMAActivity"]
originalDataset = pd.merge(originalDataset, maActivityData, how='left', on=['monthid', 'cusip6']).reset_index(drop=True)
print(originalDataset.shape)
print(originalDataset['beta_5y'].mean())

# Merging Hiring Rate and Raw Div Amount Cash
monthly_crsp_data = crsp_monthly[["cusip", "monthid", "STOCK_SPLIT", "DIVAMT", "SPREAD"]].copy()
monthly_crsp_data.columns = ["cusip8", "monthid", "STOCK_SPLIT", "DIVAMT", "SPREAD"]
originalDataset = pd.merge(originalDataset, monthly_crsp_data, how='left', on=['monthid', 'cusip8']).reset_index(drop=True)
print(originalDataset.shape)
print(originalDataset['beta_5y'].mean())

# Merging Quarterly Ohlson's O-Score
an_compustat_o_score = an_compustat[["CUSIP", "YYYYQQ_1", "O_SCORE_Q"]].copy()
an_compustat_o_score.columns = ["cusip", "yyyyqq", "O_SCORE_Q"]
originalDataset = pd.merge(originalDataset, an_compustat_o_score, how='left', on=['yyyyqq', 'cusip']).reset_index(drop=True)

print(originalDataset.shape)
print(originalDataset['beta_5y'].mean())

# Merging Hiring Rate Data and Investment Growth Data
an_compustat_yearly_data = an_compustat_yearly[["CUSIP", "DATEYEAR", "HIRING_RATE", "INVESTMENT_GROWTH_3Y"]].copy()
an_compustat_yearly_data.columns = ["cusip", "YEAR", "HIRING_RATE", "INVESTMENT_GROWTH_3Y"]
originalDataset = pd.merge(originalDataset, an_compustat_yearly_data, how='left', on=['YEAR', 'cusip']).reset_index(drop=True)

originalDataset = originalDataset.dropna(subset=["cusip"])

print(originalDataset.shape)
print(originalDataset['beta_5y'].mean())

originalDataset = originalDataset.drop_duplicates(subset=['permno', 'yyyymm', 'cusip'])
originalDataset.to_csv("dataset_files/provided_dataset_merged_df.csv", index = False)

(440720, 75)
1.0904219033731897
(440720, 81)
1.0904219033731897
(440720, 82)
1.0904219033731897
(442112, 85)
1.089601320253868
(442112, 86)
1.089601320253868
(454351, 88)
1.070776603637191
